### MMAI 5400 Assignment 3

Yuntong Zhu, Xinyuan Liang, Jiawen Li

In [1]:
import pandas as pd

In [2]:
pip install torch torchvision torchaudio

Note: you may need to restart the kernel to use updated packages.


In [3]:
import torch

#### Import data

In [4]:
data = pd.read_csv('/Users/jiawenli/Desktop/MMAI 5400/Assignment 3/A3_reviews.csv', delimiter='\t')

#### Extract reviews from the table and turn it into a list

In [5]:
reviews = data['Review'].to_list()

In [6]:
reviews

["I was tasked with finding a spot for a group dinner of eight and landed on Playa Cabana. It was pretty easy to make a reservation via their email system and our table was ready upon arrival. I don't know why I was expecting more of a kitschy Mexican restaurant, but that's not what we got. Instead, it was very intimate and cozy and the service was stellar... We had a great night!\n\nTo start, we opted for some guac which was tasty and had a nice little kick to it. To eat, I split the elotes a la parrilla and an order of tacos al pastor with my husband. The soft tacos come in an order of three but you can add on a fourth, so we did that to share evenly. It was the perfect amount of food for us, especially since the tortilla chips kept flowing! The pork in the tacos was seasoned very well. I'm used to the meat being cubed rather than in strips, so this was different but still tasty. They really packed in the filling, so I left super full. \n\nTo sip, we shared pitches of mojitos which w

#### Step 1
Use the NER model to locate the dishes in a given review.

In [7]:
pip install spacy

Note: you may need to restart the kernel to use updated packages.


Load the custom trained NER model from local

In [8]:
import spacy

# specify the model path
model_path = '/Users/jiawenli/Desktop/MMAI 5400/Assignment 3/model-best'

# load the model from my local path
nlp = spacy.load(model_path)


/Users/jiawenli/anaconda3/lib/python3.10/site-packages/spacy/util.py:910: UserWarning: [W095] Model 'en_pipeline' (0.0.0) was trained with spaCy v3.5.1 and may not be 100% compatible with the current version (3.7.2). If you see errors or degraded performance, download a newer compatible model or retrain your custom model with the current spaCy version. For more details and available updates, run: python -m spacy validate
  warnings.warn(warn_msg)


Go through each review in this reviews list，Processes each revew and prints the recognized entities.

In [9]:
# Go through each review in this reviews list，Processes each revew and prints the recognized entities.
for review in reviews:
    doc = nlp(review)
    print(f"Text: {review}")
    for ent in doc.ents:
        print(f"  Entity: {ent.text}, Type: {ent.label_}")
    print("---")

Text: I was tasked with finding a spot for a group dinner of eight and landed on Playa Cabana. It was pretty easy to make a reservation via their email system and our table was ready upon arrival. I don't know why I was expecting more of a kitschy Mexican restaurant, but that's not what we got. Instead, it was very intimate and cozy and the service was stellar... We had a great night!

To start, we opted for some guac which was tasty and had a nice little kick to it. To eat, I split the elotes a la parrilla and an order of tacos al pastor with my husband. The soft tacos come in an order of three but you can add on a fourth, so we did that to share evenly. It was the perfect amount of food for us, especially since the tortilla chips kept flowing! The pork in the tacos was seasoned very well. I'm used to the meat being cubed rather than in strips, so this was different but still tasty. They really packed in the filling, so I left super full. 

To sip, we shared pitches of mojitos which w

Add tags to the review that indicates the start and end of the dish. Store it as tagged_reviews

In [10]:
# Add tags to dishes in comments
def add_tags(text, doc):
    tagged_text = ""
    last_idx = 0
    for ent in doc.ents:
        if ent.label_ == 'DISH':
            tagged_text += text[last_idx:ent.start_char]
            # Add start label, entity, end label
            tagged_text += f"[B-ASP]{ent.text}[E-ASP]"
            last_idx = ent.end_char
    # Add the rest of the text
    tagged_text += text[last_idx:]
    return tagged_text

# Create a list to store the tagged reviews
tagged_reviews = []
for review in reviews:
    doc = nlp(review)
    tagged_review = add_tags(review, doc)
    tagged_reviews.append(tagged_review)

# Print the tagged reviews
for review in tagged_reviews:
    print(review)

I was tasked with finding a spot for a group dinner of eight and landed on Playa Cabana. It was pretty easy to make a reservation via their email system and our table was ready upon arrival. I don't know why I was expecting more of a kitschy Mexican restaurant, but that's not what we got. Instead, it was very intimate and cozy and the service was stellar... We had a great night!

To start, we opted for some [B-ASP]guac[E-ASP] which was tasty and had a nice little kick to it. To eat, I split the elotes a la parrilla and an order of [B-ASP]tacos al pastor[E-ASP] with my husband. The soft [B-ASP]tacos[E-ASP] come in an order of three but you can add on a fourth, so we did that to share evenly. It was the perfect amount of food for us, especially since the [B-ASP]tortilla chips[E-ASP] kept flowing! The pork in the [B-ASP]tacos[E-ASP] was seasoned very well. I'm used to the meat being cubed rather than in strips, so this was different but still tasty. They really packed in the filling, so I

Pass the tagged reviews as input to pyabsa.tasks.AspectPolarityClassification.SentimentClassifier.

In [11]:
!pip install pyabsa -U
from pyabsa import AspectPolarityClassification as APC

No CUDA GPU found in your device


/bin/sh: nvidia-smi: command not found
/Users/jiawenli/anaconda3/lib/python3.10/site-packages/tqdm/auto.py:22: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


[2023-11-29 17:26:03] (2.3.4) PyABSA(2.3.4): If your code crashes on Colab, please use the GPU runtime. Then run "pip install pyabsa[dev] -U" and restart the kernel.
Or if it does not work, you can use v1.x versions, e.g., pip install pyabsa<2.0 -U




Try to downgrade transformers<=4.29.0.






Load a pre-trained sentiment classifier

In [12]:
from pyabsa.tasks.AspectPolarityClassification import SentimentClassifier

/Users/jiawenli/anaconda3/lib/python3.10/multiprocessing/pool.py:268: ResourceWarning: unclosed running multiprocessing pool <multiprocessing.pool.Pool state=RUN pool_size=1>
  _warn(f"unclosed running multiprocessing pool {self!r}",


Pass tagged reviews into the Sentiment Classifier

In [13]:
from pyabsa import available_checkpoints

ckpts = available_checkpoints()
# find a suitable checkpoint and use the name:
sentiment_classifier = APC.SentimentClassifier(
    checkpoint="english"
)  # here I use the english checkpoint which is trained on all English datasets in PyABSA

[2023-11-29 17:26:17] (2.3.4) Please specify the task code, e.g. from pyabsa import TaskCodeOption
[2023-11-29 17:26:17] (2.3.4) Downloading checkpoint:english 
[2023-11-29 17:26:17] (2.3.4) Notice: The pretrained model are used for testing, it is recommended to train the model on your own custom datasets
[2023-11-29 17:26:17] (2.3.4) Checkpoint already downloaded, skip
[2023-11-29 17:26:18] (2.3.4) Load sentiment classifier from checkpoints/APC_ENGLISH_CHECKPOINT/fast_lcf_bert_English_acc_84.65_f1_82.39
[2023-11-29 17:26:18] (2.3.4) config: checkpoints/APC_ENGLISH_CHECKPOINT/fast_lcf_bert_English_acc_84.65_f1_82.39/fast_lcf_bert.config
[2023-11-29 17:26:18] (2.3.4) state_dict: checkpoints/APC_ENGLISH_CHECKPOINT/fast_lcf_bert_English_acc_84.65_f1_82.39/fast_lcf_bert.state_dict
[2023-11-29 17:26:18] (2.3.4) model: None
[2023-11-29 17:26:18] (2.3.4) tokenizer: checkpoints/APC_ENGLISH_CHECKPOINT/fast_lcf_bert_English_acc_84.65_f1_82.39/fast_lcf_bert.tokenizer
[2023-11-29 17:26:18] (2.3.4)

/Users/jiawenli/anaconda3/lib/python3.10/site-packages/transformers/convert_slow_tokenizer.py:473: UserWarning: The sentencepiece tokenizer that you are converting to a fast tokenizer uses the byte fallback option which is not implemented in the fast tokenizers. In practice this means that the fast version of the tokenizer can produce unknown tokens whereas the sentencepiece version would have converted these unknown tokens into a sequence of byte tokens matching the original piece of text.
  warnings.warn(


In [15]:
examples = [
    "everything is always cooked to perfection , the [B-ASP]service[E-ASP] is excellent , the [B-ASP]decor[E-ASP] cool and understated . $LABEL$ Positive, Positive",
    "Great [B-ASP]taste[E-ASP] ever tried."
    "I think this laptop is great!",  # if you dont label an aspect, then pyabsa try to give you a 'global sentiment'. But please avoid doing that.
]
for ex in examples:
    sentiment_classifier.predict(
        text=ex,
        print_result=True,
        ignore_error=True,  # ignore an invalid example, if it is False, invalid examples will raise Exceptions
        eval_batch_size=32,
    )

[2023-11-29 17:33:05] (2.3.4) Example 0: everything is always cooked to perfection , the <service:Positive(confidence:0.998, ref:Positive)> is excellent , the <decor:Positive(confidence:0.997, ref:Positive)> cool and understated .
[2023-11-29 17:33:05] (2.3.4) Warning: reference sentiment does not exist or its number 0 is not equal to aspect number 1, text: Great [B-ASP]taste[E-ASP] ever tried.I think this laptop is great!
[2023-11-29 17:33:05] (2.3.4) Example 0: Great <taste:Positive(confidence:0.996, ref:-100)> ever tried.I think this laptop is great!


Extract 10 reviews from the tagged_reviews list and use our SentimentClassiffier to predict, the purpose is just to see if the result is what we want.

In [17]:
extracted_tagged_reviews = tagged_reviews[:10]

for tag_review in extracted_tagged_reviews:
    sentiment_classifier.predict(
        text=tag_review,
        print_result=True,
        ignore_error=True,
        eval_batch_size=32,
    )

[2023-11-29 17:53:36] (2.3.4) Warning: reference sentiment does not exist or its number 0 is not equal to aspect number 6, text: I was tasked with finding a spot for a group dinner of eight and landed on Playa Cabana. It was pretty easy to make a reservation via their email system and our table was ready upon arrival. I don't know why I was expecting more of a kitschy Mexican restaurant, but that's not what we got. Instead, it was very intimate and cozy and the service was stellar... We had a great night!

To start, we opted for some [B-ASP]guac[E-ASP] which was tasty and had a nice little kick to it. To eat, I split the elotes a la parrilla and an order of [B-ASP]tacos al pastor[E-ASP] with my husband. The soft [B-ASP]tacos[E-ASP] come in an order of three but you can add on a fourth, so we did that to share evenly. It was the perfect amount of food for us, especially since the [B-ASP]tortilla chips[E-ASP] kept flowing! The pork in the [B-ASP]tacos[E-ASP] was seasoned very well. I'm u

/Users/jiawenli/anaconda3/lib/python3.10/site-packages/sklearn/metrics/_classification.py:1344: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/Users/jiawenli/anaconda3/lib/python3.10/site-packages/sklearn/metrics/_classification.py:1344: UndefinedMetricWarning: Recall and F-score are ill-defined and being set to 0.0 in labels with no true samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/Users/jiawenli/anaconda3/lib/python3.10/site-packages/sklearn/metrics/_classification.py:1344: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/Users/jiawenli/anaconda3/l

[2023-11-29 17:53:37] (2.3.4) Example 0: As a Mexican I always crave authentic Mexican food in Toronto but have difficulties finding it. Playa Cabana is very good and does a an amazing job at keeping things as authentic as possible.

Today at lunch I had the <chips and salsa:Positive(confidence:0.945, ref:-100)> which were yummy. The Playa Burrito with Pork Carnitas was also very good. The green salsa was a bit citrusy but overall very good. I would order it again.

This is definitely a place
[2023-11-29 17:53:37] (2.3.4) Example 1: finding it. Playa Cabana is very good and does a an amazing job at keeping things as authentic as possible.

Today at lunch I had the chips and salsa which were yummy. The Playa <Burrito:Positive(confidence:0.971, ref:-100)> with <Pork Carnitas:Positive(confidence:0.969, ref:-100)> was also very good. The green salsa was a bit citrusy but overall very good. I would order it again.

This is definitely a place to come back for some great Mexican food. Staff w

#### Develop an absa function to take reviews as input for sentiment analysis and then return a dataframe.

In [29]:
import pandas as pd
from pyabsa import AspectPolarityClassification as APC, available_checkpoints

def find_dishes(review):
    dishes = []
    start_tag = '[B-ASP]'
    end_tag = '[E-ASP]'
    while start_tag in review and end_tag in review:
        start_index = review.find(start_tag) + len(start_tag)
        end_index = review.find(end_tag)
        dish = review[start_index:end_index].strip()
        dishes.append(dish)
        review = review[end_index + len(end_tag):]
    return dishes


In [34]:
def absa(reviews):
    ckpts = available_checkpoints()
    
    sentiment_classifier = APC.SentimentClassifier(checkpoint="english")

    results_df = pd.DataFrame(columns=['review_id', 'dish', 'sentiment', 'confidence'])

    for idx, review in enumerate(reviews):
        dishes = find_dishes(review)

        for dish in dishes:
            sentiment_result = sentiment_classifier.predict(
                text=dish,
                print_result=True,
                ignore_error=True,
                eval_batch_size=32,
            )
            
            if isinstance(sentiment_result, dict) and 'sentiment' in sentiment_result:
                sentiment = sentiment_result['sentiment'][0] if sentiment_result['sentiment'] else ''
                confidence = sentiment_result['confidence'][0] if sentiment_result['confidence'] else 0.0
                confidence = round(float(confidence), 2)

                results_df = results_df.append({
                    'review_id': idx,
                    'dish': dish,
                    'sentiment': sentiment,
                    'confidence': confidence
                }, ignore_index=True)
            else:
                print(f"Unexpected format of sentiment result for dish: {dish}")

    return results_df



In [35]:
absa(tagged_reviews[:20])

[2023-11-29 18:41:18] (2.3.4) Please specify the task code, e.g. from pyabsa import TaskCodeOption
[2023-11-29 18:41:19] (2.3.4) Downloading checkpoint:english 
[2023-11-29 18:41:19] (2.3.4) Notice: The pretrained model are used for testing, it is recommended to train the model on your own custom datasets
[2023-11-29 18:41:19] (2.3.4) Checkpoint already downloaded, skip
[2023-11-29 18:41:19] (2.3.4) Load sentiment classifier from checkpoints/APC_ENGLISH_CHECKPOINT/fast_lcf_bert_English_acc_84.65_f1_82.39
[2023-11-29 18:41:19] (2.3.4) config: checkpoints/APC_ENGLISH_CHECKPOINT/fast_lcf_bert_English_acc_84.65_f1_82.39/fast_lcf_bert.config
[2023-11-29 18:41:19] (2.3.4) state_dict: checkpoints/APC_ENGLISH_CHECKPOINT/fast_lcf_bert_English_acc_84.65_f1_82.39/fast_lcf_bert.state_dict
[2023-11-29 18:41:19] (2.3.4) model: None
[2023-11-29 18:41:19] (2.3.4) tokenizer: checkpoints/APC_ENGLISH_CHECKPOINT/fast_lcf_bert_English_acc_84.65_f1_82.39/fast_lcf_bert.tokenizer
[2023-11-29 18:41:19] (2.3.4)

/Users/jiawenli/anaconda3/lib/python3.10/site-packages/transformers/convert_slow_tokenizer.py:473: UserWarning: The sentencepiece tokenizer that you are converting to a fast tokenizer uses the byte fallback option which is not implemented in the fast tokenizers. In practice this means that the fast version of the tokenizer can produce unknown tokens whereas the sentencepiece version would have converted these unknown tokens into a sequence of byte tokens matching the original piece of text.
  warnings.warn(


[2023-11-29 18:41:23] (2.3.4) Warning: reference sentiment does not exist or its number 0 is not equal to aspect number 1, text:  [B-ASP]Global Sentiment[E-ASP] guac
[2023-11-29 18:41:23] (2.3.4) Example 0: guac
[2023-11-29 18:41:23] (2.3.4) Warning: reference sentiment does not exist or its number 0 is not equal to aspect number 1, text:  [B-ASP]Global Sentiment[E-ASP] tacos al pastor
[2023-11-29 18:41:23] (2.3.4) Example 0: tacos al pastor
[2023-11-29 18:41:23] (2.3.4) Warning: reference sentiment does not exist or its number 0 is not equal to aspect number 1, text:  [B-ASP]Global Sentiment[E-ASP] tacos


/var/folders/zj/_4td97xs5m5_42chzkdpgsch0000gn/T/ipykernel_30634/65532618.py:24: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  results_df = results_df.append({
/var/folders/zj/_4td97xs5m5_42chzkdpgsch0000gn/T/ipykernel_30634/65532618.py:24: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  results_df = results_df.append({
/var/folders/zj/_4td97xs5m5_42chzkdpgsch0000gn/T/ipykernel_30634/65532618.py:24: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  results_df = results_df.append({


[2023-11-29 18:41:23] (2.3.4) Example 0: tacos
[2023-11-29 18:41:23] (2.3.4) Warning: reference sentiment does not exist or its number 0 is not equal to aspect number 1, text:  [B-ASP]Global Sentiment[E-ASP] tortilla chips
[2023-11-29 18:41:24] (2.3.4) Example 0: tortilla chips
[2023-11-29 18:41:24] (2.3.4) Warning: reference sentiment does not exist or its number 0 is not equal to aspect number 1, text:  [B-ASP]Global Sentiment[E-ASP] tacos
[2023-11-29 18:41:24] (2.3.4) Example 0: tacos
[2023-11-29 18:41:24] (2.3.4) Warning: reference sentiment does not exist or its number 0 is not equal to aspect number 1, text:  [B-ASP]Global Sentiment[E-ASP] tacos


...

[2023-11-29 18:41:33] (2.3.4) Example 0: guacamole
[2023-11-29 18:41:33] (2.3.4) Warning: reference sentiment does not exist or its number 0 is not equal to aspect number 1, text:  [B-ASP]Global Sentiment[E-ASP] octopus tacos
[2023-11-29 18:41:33] (2.3.4) Example 0: octopus tacos
[2023-11-29 18:41:33] (2.3.4) Warning: reference sentiment does not exist or its number 0 is not equal to aspect number 1, text:  [B-ASP]Global Sentiment[E-ASP] crab cakes
[2023-11-29 18:41:33] (2.3.4) Example 0: crab cakes
[2023-11-29 18:41:33] (2.3.4) Warning: reference sentiment does not exist or its number 0 is not equal to aspect number 1, text:  [B-ASP]Global Sentiment[E-ASP] guacamole


/var/folders/zj/_4td97xs5m5_42chzkdpgsch0000gn/T/ipykernel_30634/65532618.py:24: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  results_df = results_df.append({
/var/folders/zj/_4td97xs5m5_42chzkdpgsch0000gn/T/ipykernel_30634/65532618.py:24: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  results_df = results_df.append({
/var/folders/zj/_4td97xs5m5_42chzkdpgsch0000gn/T/ipykernel_30634/65532618.py:24: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  results_df = results_df.append({


[2023-11-29 18:41:33] (2.3.4) Example 0: guacamole
[2023-11-29 18:41:33] (2.3.4) Warning: reference sentiment does not exist or its number 0 is not equal to aspect number 1, text:  [B-ASP]Global Sentiment[E-ASP] chips
[2023-11-29 18:41:33] (2.3.4) Example 0: chips
[2023-11-29 18:41:33] (2.3.4) Warning: reference sentiment does not exist or its number 0 is not equal to aspect number 1, text:  [B-ASP]Global Sentiment[E-ASP] tacos
[2023-11-29 18:41:34] (2.3.4) Example 0: tacos


/var/folders/zj/_4td97xs5m5_42chzkdpgsch0000gn/T/ipykernel_30634/65532618.py:24: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  results_df = results_df.append({
/var/folders/zj/_4td97xs5m5_42chzkdpgsch0000gn/T/ipykernel_30634/65532618.py:24: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  results_df = results_df.append({


review_id             dish sentiment  confidence
0           0             guac   Neutral        0.92
1           0  tacos al pastor   Neutral        0.97
2           0            tacos   Neutral        0.96
3           0   tortilla chips   Neutral        0.94
4           0            tacos   Neutral        0.96
..        ...              ...       ...         ...
110        19    octopus tacos   Neutral        0.92
111        19       crab cakes   Neutral        0.86
112        19        guacamole   Neutral        0.92
113        19            chips   Neutral        0.92
114        19            tacos   Neutral        0.96

[115 rows x 4 columns]